In [1]:
# Final AIP Charts with bells and whistles

In [2]:
# Import packages

import pandas as pd
import numpy as np

In [3]:
import altair as alt

In [4]:
# Load Kenya MTF Data 

chunksize = 10

mtf_list = []
chunksize = 10
for chunk in pd.read_csv("kenya_mtf.csv", encoding='latin-1', chunksize = chunksize):
    mtf_list.append(chunk)
    
kenya_mtf = pd.concat(mtf_list, axis=0)
kenya_mtf = pd.DataFrame(data = kenya_mtf)

In [5]:
# Tools

import functools
def conjunction(*conditions):
    return functools.reduce(np.logical_and, conditions)

In [6]:
def catalyst(*args, **kwargs):
    font = "Times New Roman"
    labelFont = "Times New Roman" 
    sourceFont = "Times New Roman"
    # Axes
    axisColor = "#000000"
    gridColor = "#DEDDDD"
    # Colors
    main_palette = [   '#2980B9', #(light blue)
        '#003366', #(dark blue)
        '#FFAE19', #(gold)
        '#D68910', #(dark gold)
        '#E67E22', #(orange)
        '#D35400', #(dark orange)
        '#FF4500', #(red)
        '#FF6162', #(dark pink/red)
        '#438B28', #(green)
        '#45B39D', #(teal)
        '#99ADC1', #(light gray)
        '#212F3C', #(dark gray)
    ]
    return {
        "width": 800, 
        "height": 400, 
        "config": {
            "title": {
                "fontSize": 18,
                "font": font,
                "anchor": "center",
                "fontColor": "#000000",
            },
            "axisX": {
                "domain": True,
                "domainColor": axisColor,
                #"domainWidth": 1,
                "grid": False,
                "labelFont": labelFont,
                "labelFontSize": 14,
                #"labelAngle": 0,
                #"tickColor": axisColor,
                #"tickSize": 5, 
                "titleFont": font,
                "titleFontSize": 14,
                "titleFontWeight": "normal",
                #"titlePadding": 10, 
                "title": "X Axis Title (units)", 
                #"titleAngle":0
            },
            "axisY": {
                "domain": True,
                "grid": False,
                "gridColor": gridColor,
                "gridWidth": 1,
                "labelFont": labelFont,
                "labelFontSize": 14,
                "labelAngle": 0,
                "ticks": False, 
                "titleFont": font,
                "titleFontSize": 14,
                "titleFontWeight": "normal",
                "titlePadding": 10, 
                "title": "Y Axis Title (units)",
                #"titleY": -10, 
                #"titleX": 18,
                #"titleAngle": 0 #-90
            },
            "range": {
                "category": main_palette
            },
            "legend": {
                "labelFont": labelFont,
                "labelFontSize": 14,
                "symbolType": "square", 
                "symbolSize": 100, 
                "titleFont": font,
                "titleFontSize": 14,
                "titleFontWeight": "normal",
                "title": "Legend", 
                "orient": "right", 
                "offset": 0, 
            },
            "tooltip":{
                "font": "Open Sans"
            },
            "view": {
                "stroke": "transparent", 
        ### MARKS CONFIGURATIONS ###
           "text": {
               "font": "Times New Roman",
               "color": main_palette,
               "fontSize": 14,
               "align": "right",
               "fontWeight": 400,
               "size": 14,
           }, 
           "bar": {
                "size": 40,
                "binSpacing": 1,
                "continuousBandSize": 30,
                "discreteBandSize": 30,
                "fill": main_palette,
                "stroke": False,
           },
            }
        }
    }

In [7]:
alt.themes.register('catalyst', catalyst)
alt.themes.enable('catalyst');

In [ ]:
#                                         range=['#2980B9', #(light blue)
#                                                '#003366', #(dark blue)
#                                                '#FFAE19', #(gold)
#                                                '#D68910', #(dark gold)
#                                                '#E67E22', #(orange)
#                                                '#D35400', #(dark orange)
#                                                '#FF4500', #(red)
#                                                '#FF6162', #(dark pink/red)
#                                                '#438B28', #(green)
#                                                '#45B39D', #(teal)
#                                                '#99ADC1', #(light gray)
#                                                '#212F3C', #(dark gray)

In [7]:
data = pd.DataFrame({
    'x': range(12),
    'color': [   '#2980B9', #(light blue)
        '#003366', #(dark blue)
        '#FFAE19', #(gold)
        '#D68910', #(dark gold)
        '#E67E22', #(orange)
        '#D35400', #(dark orange)
        '#FF4500', #(red)
        '#FF6162', #(dark pink/red)
        '#438B28', #(green)
        '#45B39D', #(teal)
        '#99ADC1', #(light gray)
        '#212F3C', #(dark gray)
    ]
})

alt.Chart(data).mark_point(
    filled=True,
    size=200
).encode(
    x='x',
    color=alt.Color('color', scale=None)
).properties(
    height = 100
)

alt.Chart(...)

In [33]:
# electricity_access_tiers2.html 
# renamed Primary Sources of Electricity by Tier

alt.data_transformers.disable_max_rows()
source = kenya_mtf[kenya_mtf[['c_c_159', 'locality_ur', 'elc_access', 'elc_aggr_tier', 'Primary_1st_fuel', 'Primary_stove_type']].notnull().all(1)]

# data source

col1 = source['locality_ur'] != 'NaN'
col2 = source['elc_access'] != 'NaN'
col3 = source['c_c_159'] != 'NaN'
col4 = source['Primary_1st_fuel'] != 'NaN'
col5 = source['Primary_stove_type'] != 'NaN'
col6 = source['elc_aggr_tier'] != "NaN"

source = source[conjunction(col1,col2, col3, col4, col5, col6)]
df = source[['elc_aggr_tier', 'locality_ur',
             'Primary_1st_fuel', 'Primary_stove_type', 
             'hh_grid', 'c_c_159', 'elc_access']]

# chart
chart = alt.Chart(df).transform_joinaggregate(
    total = 'count(*)'
).transform_calculate(
    pct = '1 / datum.total'
).encode(
    x = alt.X('elc_aggr_tier', axis = alt.Axis(title = '')),
    y = alt.Y('sum(pct):Q', axis = alt.Axis(title = "", format ='%')),
    color = alt.Color('c_c_159:N', 
                      scale = alt.Scale(domain=['Generator (Connecting one or more households)',
                                                'Local mini-grid', 'National grid', 'No electricity',
                                               'Other', 'Pico-Hydro','Rechargeable Battery', 
                                               'Solar Home System', 'Solar Lantern/Lighting System'], 
                                        
                                        range=["#2980B9", 
                                               "#003366","#438B28", "#FF4500",
                                               "#FFAE19", "#FF6162", "#45B39D",
                                               "#99ADC1", "#212F3C"]), # colors here
                      
                      title = ' '),
    tooltip = [alt.Tooltip('c_c_159:N', title = "Electricity Source"), 
               alt.Tooltip('sum(pct):Q', format = '.2%', title = "Percentage")]
).properties(
    height = 500,
    width = 800
)

# Locality Filter

locality_options = [None, 'Urban', 'Rural']
locality_labels = ['National', 'Urban', 'Rural']

locality_dropdown=alt.binding_select(
    options= locality_options, 
    labels = locality_labels, 
    name = "Locality Breakdown  ")
locality_select=alt.selection_single(
    fields=['locality_ur'],
    bind=locality_dropdown)


# Primary cooking fuel

cooking_options = [None, 'Firewood', 'Charcoal', 'LPG/cooking gas', 'Kerosene',
                    'Biomass Briquette', 'Electricity', 'Biogas', 
                    'Coal/lignite', 'Processed biomass (pellets)/ woodchips1']

cooking_labels = ['All responses', 'Firewood', 'Charcoal', 'LPG/cooking gas', 'Kerosene', 
                    'Biomass Briquette', 'Electricity', 'Biogas', 
                    'Coal/lignite', 'Processed biomass']

cooking_dropdown = alt.binding_select(
    options = cooking_options, 
    labels = cooking_labels, 
    name = "Primary source of cooking fuel  ")

cooking_select=alt.selection_single(
    fields=['Primary_1st_fuel'],
    bind=cooking_dropdown)

# Primary cookstove filter

cookstove_options = [None, 'Three stone/Open fire',
                'Manufactured stove',
                'Other Self-Built Stove',
                'Other']

cookstove_labels = ['All responses', 'Three stone/Open fire',
                'Manufactured stove',
                'Self-Built Stove',
                'Other']

cookstove_dropdown = alt.binding_select(
    options = cookstove_options, 
    labels = cookstove_labels, 
    name = "Primary cookstove type ")

cookstove_select=alt.selection_single(
    fields=['Primary_stove_type'],
    bind=cookstove_dropdown)

# Primary lighting filter 

lighting_options = [None, 
                    'National grid',
                   'Rechargeable Battery',
                   'No electricity', 
                   'Solar Lantern/Lighting System',
                   'Solar Home System',
                   'Generator (Connecting one or more households)',
                   'Other']

lighting_labels = ['All responses', 
                   'National grid',
                   'Rechargeable Battery',
                   'No electricity'
                   'Solar Lantern/Lighting System',
                   'Solar Home System',
                   'Generator',
                   'Other']

lighting_dropdown = alt.binding_select(
    options = lighting_options, 
    labels = lighting_labels, 
    name = "Primary source of electricity  ")

lighting_select=alt.selection_single(
    fields=['c_c_159'],
    bind=lighting_dropdown)

# Connected to the national grid filter

grid_options = [None, 'Yes', 'No']
grid_labels = ['All responses', 'Yes', 'No']

grid_dropdown=alt.binding_select(
    options= grid_options, 
    labels = grid_labels, 
    name = "Is the household connected to the national grid?  ")
grid_select=alt.selection_single(
    fields=['hh_grid'],
    bind=grid_dropdown)

# Chart with bells and whistles

chart = (chart.mark_bar() + chart.mark_text(
    align = 'center', baseline='bottom', dy = -5)
).add_selection( # Sixth, cookstove filter
    cookstove_select
).transform_filter(
    cookstove_select
).add_selection( # Fifth, cooking fuel filter
    cooking_select
).transform_filter(
    cooking_select
# ).add_selection( # Fourth, primary source of lighting
#     lighting_select
# ).transform_filter(
#     lighting_select  
).add_selection( # Third, grid connection filter
    grid_select
).transform_filter(
    grid_select
).add_selection( # First, locality filter
    locality_select
).transform_filter(
    locality_select
)

chart = chart.properties(
    title={
      "text": ["Primary Sources of Electricity by Tier"],
      "color": "black",
        "font": 'Times New Roman'
    }
)

final = alt.concat(chart,
    title=alt.TitleParams(
        ['', '',  
         'This chart includes responses from 81.77% of households in the Kenya MTF survey sample (total size = 4,590).',
         'Use the dropdown filters to interact with the data.'],
        baseline='bottom',
        orient='bottom',
        anchor='start',
        font = 'Times New Roman',
        fontWeight='normal',
        fontStyle = "italic",
        fontSize=15)
)

final = final.configure(font = 'Times New Roman')
final


alt.ConcatChart(...)

In [49]:
df.shape[0] / kenya_mtf.shape[0]

0.8177621455264893

In [34]:
final.save('Primary Sources of Electricity by Tier.html')

In [35]:
final.save('Primary Sources of Electricity by Tier.json')

In [72]:
# primary_cooking.html
# NOT USED

alt.data_transformers.disable_max_rows()
source = kenya_mtf[kenya_mtf[['c_c_159', 'locality_ur', 'elc_access', 'Primary_1st_fuel', 'Primary_stove_type']].notnull().all(1)]

# data source

col1 = source['locality_ur'] != 'NaN'
col2 = source['elc_access'] != 'NaN'
col3 = source['c_c_159'] != 'NaN'
col4 = source['Primary_1st_fuel'] != 'NaN'
col5 = source['Primary_stove_type'] != 'NaN'

source = source[conjunction(col1,col2, col3, col4, col5)]
df = source[['elc_aggr_tier', 'locality_ur',
             'Primary_1st_fuel', 'Primary_stove_type', 
             'hh_grid', 'c_c_159', 'elc_access']]

# chart
chart = alt.Chart(df).transform_joinaggregate(
    total = 'count(*)'
).transform_calculate(
    pct = '1 / datum.total'
).encode(
    
    x = alt.X('elc_aggr_tier', axis = alt.Axis(title = '')),
    y = alt.Y('sum(pct):Q', axis = alt.Axis(title = "", format ='%')),
    
    color = alt.Color('Primary_1st_fuel:N', 
                      
                      scale = alt.Scale(domain=['Biogas', 
                                                'Biomass Briquette', 
                                                'Charcoal', 
                                                'Coal/lignite',
                                                'Crop Residue/Plant Biomass', 
                                                'Electricity', 
                                                'Firewood',
                                                'Kerosene', 
                                                'LPG/cooking gas', 
                                                'Not applicable', 
                                                'Processed biomass (pellets)/ woodchips1'], 
                      
                                        range=['#2980B9', #(light blue)
                                               '#003366', #(dark blue)
                                               '#FFAE19', #(gold)
                                               '#D68910', #(dark gold)
                                               '#E67E22', #(orange)
                                               '#D35400', #(dark orange)
                                               '#FF4500', #(red)
                                               '#FF6162', #(dark pink/red)
                                               '#438B28', #(green)
                                               '#45B39D', #(teal)
                                               '#99ADC1', #(light gray)
                                               '#212F3C'] #(dark gray)
                                       )
                                       ), 
                      
    tooltip = [alt.Tooltip('Primary_1st_fuel:N', title = "Primary source of cooking fuel"), 
               alt.Tooltip('sum(pct):Q', format = '.2%', title = "Percentage")]
).properties(
    height = 500,
    width = 800
)

# Locality Filter

locality_options = [None, 'Urban', 'Rural']
locality_labels = ['National', 'Urban', 'Rural']

locality_dropdown=alt.binding_select(
    options= locality_options, 
    labels = locality_labels, 
    name = "Locality Breakdown  ")
locality_select=alt.selection_single(
    fields=['locality_ur'],
    bind=locality_dropdown)


# Primary cooking fuel

cooking_options = [None, 'Firewood', 'Charcoal', 'LPG/cooking gas', 'Kerosene',
                    'Biomass Briquette', 'Electricity', 'Biogas', 
                    'Coal/lignite', 'Processed biomass (pellets)/ woodchips1']

cooking_labels = ['All responses', 'Firewood', 'Charcoal', 'LPG/cooking gas', 'Kerosene', 
                    'Biomass Briquette', 'Electricity', 'Biogas', 
                    'Coal/lignite', 'Processed biomass']

cooking_dropdown = alt.binding_select(
    options = cooking_options, 
    labels = cooking_labels, 
    name = "Primary source of cooking fuel  ")

cooking_select=alt.selection_single(
    fields=['Primary_1st_fuel'],
    bind=cooking_dropdown)

# Primary cookstove filter

cookstove_options = [None, 'Three stone/Open fire',
                'Manufactured stove',
                'Other Self-Built Stove',
                'Other']

cookstove_labels = ['All responses', 'Three stone/Open fire',
                'Manufactured stove',
                'Self-Built Stove',
                'Other']

cookstove_dropdown = alt.binding_select(
    options = cookstove_options, 
    labels = cookstove_labels, 
    name = "Primary cookstove type ")

cookstove_select=alt.selection_single(
    fields=['Primary_stove_type'],
    bind=cookstove_dropdown)

# Primary lighting filter 

lighting_options = [None, 
                    'National grid',
                   'Rechargeable Battery',
                   'No electricity', 
                   'Solar Lantern/Lighting System',
                   'Solar Home System',
                   'Generator (Connecting one or more households)',
                   'Other']

lighting_labels = ['All responses', 
                   'National grid',
                   'Rechargeable Battery',
                   'No electricity',
                   'Solar Lantern/Lighting System',
                   'Solar Home System',
                   'Generator',
                   'Other']

lighting_dropdown = alt.binding_select(
    options = lighting_options, 
    labels = lighting_labels, 
    name = "Primary source of electricity  ")

lighting_select=alt.selection_single(
    fields=['c_c_159'],
    bind=lighting_dropdown)

# Connected to the national grid filter

grid_options = [None, 'Yes', 'No']
grid_labels = ['All responses', 'Yes', 'No']

grid_dropdown=alt.binding_select(
    options= grid_options, 
    labels = grid_labels, 
    name = "Is the household connected to the national grid?  ")
grid_select=alt.selection_single(
    fields=['hh_grid'],
    bind=grid_dropdown)

# Chart with bells and whistles

chart = (chart.mark_bar() + chart.mark_text(
    align = 'center', baseline='bottom', dy = -5)
).add_selection( # Sixth, cookstove filter
    cookstove_select
).transform_filter(
    cookstove_select
# ).add_selection( # Fifth, cooking fuel filter
#     cooking_select
# ).transform_filter(
#     cooking_select
).add_selection( # Fourth, primary source of lighting
    lighting_select
).transform_filter(
    lighting_select  
).add_selection( # Third, grid connection filter
    grid_select
).transform_filter(
    grid_select
).add_selection( # First, locality filter
    locality_select
).transform_filter(
    locality_select
)

chart = chart.properties(
    title={
      "text": ["Primary Sources of Cooking Fuel by Electricity Access Tier"],
      "color": "black",
        "font": 'Times New Roman'
    }
)

final = alt.concat(chart,
    title=alt.TitleParams(
        ['', '',  
         'This chart includes responses from 81.77% of households in the Kenya MTF survey sample (total size = 4,590).',
         'Use the dropdown filters to interact with the data.'],
        baseline='bottom',
        orient='bottom',
        anchor='start',
        font = 'Times New Roman',
        fontWeight='normal',
        fontStyle = "italic",
        fontSize=15)
)

final = final.configure(font = 'Times New Roman')
final


alt.ConcatChart(...)

In [73]:
final.save('Primary Sources of Cooking Fuel by Electricity Tier.html')

In [74]:
final.save('Primary Sources of Cooking Fuel by Electricity Tier.json')

In [84]:
# primary lighting

alt.data_transformers.disable_max_rows()
source = kenya_mtf[kenya_mtf[['c_c_159', 'locality_ur', 'elc_access', 'Primary_1st_fuel', 'Primary_stove_type']].notnull().all(1)]

# data source

col1 = source['locality_ur'] != 'NaN'
col2 = source['elc_access'] != 'NaN'
col3 = source['c_c_159'] != 'NaN'
col4 = source['Primary_1st_fuel'] != 'NaN'
col5 = source['Primary_stove_type'] != 'NaN'

source = source[conjunction(col1,col2, col3, col4, col5)]
df = source[['elc_aggr_tier', 'locality_ur',
             'Primary_1st_fuel', 'Primary_stove_type', 
             'hh_grid', 'c_c_159', 'elc_access']]
#chart 

chart = alt.Chart(df).transform_joinaggregate(
    total = 'count(*)'
).transform_calculate(
    pct = '1 / datum.total'
).encode(
    x = alt.X('c_c_159',
              sort=alt.EncodingSortField(field="c_c_159", 
                                         op="count", 
                                         order='descending'),
              axis = alt.Axis(title = " ")),
    y = alt.Y('sum(pct):Q', axis = alt.Axis(title = '', format = '%')),
    tooltip = 'c_c_159'
)

#Locality filter
locality_options = [None, 'Urban', 'Rural']
locality_labels = ['National', 'Urban', 'Rural']

locality_dropdown=alt.binding_select(
    options= locality_options, 
    labels = locality_labels, 
    name = "Locality Breakdown  ")
locality_select=alt.selection_single(
    fields=['locality_ur'],
    bind=locality_dropdown)

#Tier filter
tiers = [None, 'Tier 0', 'Tier 1', 'Tier 2', 'Tier 3', 'Tier 4', 'Tier 5']
tier_labels = ['All Tiers', 'Tier 0', 'Tier 1', 'Tier 2', 'Tier 3', 'Tier 4', 'Tier 5']
tier_dropdown=alt.binding_select(options=tiers, labels = tier_labels, name = "Electricity Tier  ")
tier_select=alt.selection_single(fields=['elc_aggr_tier'],
                                bind=tier_dropdown)

# Primary cooking fuel

cooking_options = [None, 'Firewood', 'Charcoal', 'LPG/cooking gas', 'Kerosene',
                    'Biomass Briquette', 'Electricity', 'Biogas', 
                    'Coal/lignite', 'Processed biomass (pellets)/ woodchips1']

cooking_labels = ['All responses', 'Firewood', 'Charcoal', 'LPG/cooking gas', 'Kerosene', 
                    'Biomass Briquette', 'Electricity', 'Biogas', 
                    'Coal/lignite', 'Processed biomass']

cooking_dropdown = alt.binding_select(
    options = cooking_options, 
    labels = cooking_labels, 
    name = "Primary source of cooking fuel  ")

cooking_select=alt.selection_single(
    fields=['Primary_1st_fuel'],
    bind=cooking_dropdown)

# Primary cookstove filter

cookstove_options = [None, 'Three stone/Open fire',
                'Manufactured stove',
                'Other Self-Built Stove',
                'Other']

cookstove_labels = ['All responses', 'Three stone/Open fire',
                'Manufactured stove',
                'Self-Built Stove',
                'Other']

cookstove_dropdown = alt.binding_select(
    options = cookstove_options, 
    labels = cookstove_labels, 
    name = "Primary cookstove  ")

cookstove_select=alt.selection_single(
    fields=['Primary_stove_type'],
    bind=cookstove_dropdown)

# Primary lighting filter 

lighting_options = [None, 
                    'National grid',
                   'Rechargeable Battery',
                   'No electricity', 
                   'Solar Lantern/Lighting System',
                   'Solar Home System',
                   'Generator (Connecting one or more households)',
                   'Other']

lighting_labels = ['All responses', 
                   'National grid',
                   'Rechargeable Battery',
                   'No electricity',
                   'Solar Lantern/Lighting System',
                   'Solar Home System',
                   'Generator',
                   'Other']

lighting_dropdown = alt.binding_select(
    options = lighting_options, 
    labels = lighting_labels, 
    name = "Primary source of electricity  ")

lighting_select=alt.selection_single(
    fields=['c_c_159'],
    bind=lighting_dropdown)

# Connected to the national grid filter

grid_options = [None, 'Yes', 'No']
grid_labels = ['All responses', 'Yes', 'No']

grid_dropdown=alt.binding_select(
    options= grid_options, 
    labels = grid_labels, 
    name = "Is the household connected to the national grid?  ")
grid_select=alt.selection_single(
    fields=['hh_grid'],
    bind=grid_dropdown)

#chart

chart = chart.mark_bar(color = '#2980B9') + chart.mark_text(
    align = 'center', 
    baseline='bottom',
    size = 15
).encode(
    text = alt.Text('sum(pct):Q', 
                    format = '.2%')
)

chart = (chart
).add_selection( # Sixth, cookstove filter
    cookstove_select
).transform_filter(
    cookstove_select
).add_selection( # Fifth, cooking fuel filter
    cooking_select
).transform_filter(
    cooking_select 
).add_selection( # Third, grid connection filter
    grid_select
).transform_filter(
    grid_select
).add_selection( # First, locality filter
    locality_select
).transform_filter(
    locality_select
).add_selection(
    tier_select
).transform_filter( # Tier filter
    tier_select
)

chart = chart.properties(
    height = 500,
    width = 800,
    title={
      "text": ["Primary Sources of Household Lighting"],
      "color": "black",
        "font": 'Times New Roman'
    }
)

final = alt.concat(chart,
    title=alt.TitleParams(
        ['', '',  
         'This chart includes responses from 81.77% of households in the Kenya MTF survey sample (total size = 4,590).',
         'Use the dropdown filters to interact with the data.'],
        baseline='bottom',
        orient='bottom',
        anchor='start',
        font = 'Times New Roman',
        fontWeight='normal',
        fontStyle = "italic",
        fontSize=15)
)

final = final.configure(font = 'Times New Roman')
final

alt.ConcatChart(...)

In [20]:
df.shape[0] / kenya_mtf.shape[0]

0.8177621455264893

In [22]:
final.save('Primary Sources of Household Lighting.html')

In [23]:
final.save('Primary Sources of Household Lighting.json')

In [83]:
# primary lighting

alt.data_transformers.disable_max_rows()
source = kenya_mtf[kenya_mtf[['c_c_159', 'locality_ur', 'elc_access', 'Primary_1st_fuel', 'Primary_stove_type']].notnull().all(1)]

# data source

col1 = source['locality_ur'] != 'NaN'
col2 = source['elc_access'] != 'NaN'
col3 = source['c_c_159'] != 'NaN'
col4 = source['Primary_1st_fuel'] != 'NaN'
col5 = source['Primary_stove_type'] != 'NaN'

source = source[conjunction(col1,col2, col3, col4, col5)]
df = source[['elc_aggr_tier', 'locality_ur',
             'Primary_1st_fuel', 'Primary_stove_type', 
             'hh_grid', 'c_c_159', 'elc_access']]
#chart 

chart = alt.Chart(df).transform_joinaggregate(
    total = 'count(*)'
).transform_calculate(
    pct = '1 / datum.total'
).encode(
    x = alt.X('Primary_1st_fuel',
              sort=alt.EncodingSortField(field="Primary_1st_fuel", 
                                         op="count", 
                                         order='descending'),
              axis = alt.Axis(title = " ")),
    y = alt.Y('sum(pct):Q', axis = alt.Axis(title = '', format = '%')),
    tooltip = 'Primary_1st_fuel'
)

#Locality filter
locality_options = [None, 'Urban', 'Rural']
locality_labels = ['National', 'Urban', 'Rural']

locality_dropdown=alt.binding_select(
    options= locality_options, 
    labels = locality_labels, 
    name = "Locality Breakdown  ")
locality_select=alt.selection_single(
    fields=['locality_ur'],
    bind=locality_dropdown)

#Tier filter
tiers = [None, 'Tier 0', 'Tier 1', 'Tier 2', 'Tier 3', 'Tier 4', 'Tier 5']
tier_labels = ['All Tiers', 'Tier 0', 'Tier 1', 'Tier 2', 'Tier 3', 'Tier 4', 'Tier 5']
tier_dropdown=alt.binding_select(options=tiers, labels = tier_labels, name = "Electricity Tier  ")
tier_select=alt.selection_single(fields=['elc_aggr_tier'],
                                bind=tier_dropdown)

# Primary cooking fuel

cooking_options = [None, 'Firewood', 'Charcoal', 'LPG/cooking gas', 'Kerosene',
                    'Biomass Briquette', 'Electricity', 'Biogas', 
                    'Coal/lignite', 'Processed biomass (pellets)/ woodchips1']

cooking_labels = ['All responses', 'Firewood', 'Charcoal', 'LPG/cooking gas', 'Kerosene', 
                    'Biomass Briquette', 'Electricity', 'Biogas', 
                    'Coal/lignite', 'Processed biomass']

cooking_dropdown = alt.binding_select(
    options = cooking_options, 
    labels = cooking_labels, 
    name = "Primary source of cooking fuel  ")

cooking_select=alt.selection_single(
    fields=['Primary_1st_fuel'],
    bind=cooking_dropdown)

# Primary cookstove filter

cookstove_options = [None, 'Three stone/Open fire',
                'Manufactured stove',
                'Other Self-Built Stove',
                'Other']

cookstove_labels = ['All responses', 'Three stone/Open fire',
                'Manufactured stove',
                'Self-Built Stove',
                'Other']

cookstove_dropdown = alt.binding_select(
    options = cookstove_options, 
    labels = cookstove_labels, 
    name = "Primary cookstove type ")

cookstove_select=alt.selection_single(
    fields=['Primary_stove_type'],
    bind=cookstove_dropdown)

# Primary lighting filter 

lighting_options = [None, 
                    'National grid',
                   'Rechargeable Battery',
                   'No electricity', 
                   'Solar Lantern/Lighting System',
                   'Solar Home System',
                   'Generator (Connecting one or more households)',
                   'Other']

lighting_labels = ['All responses', 
                   'National grid',
                   'Rechargeable Battery',
                   'No electricity',
                   'Solar Lantern/Lighting System',
                   'Solar Home System',
                   'Generator',
                   'Other']

lighting_dropdown = alt.binding_select(
    options = lighting_options, 
    labels = lighting_labels, 
    name = "Primary source of electricity  ")

lighting_select=alt.selection_single(
    fields=['c_c_159'],
    bind=lighting_dropdown)

# Connected to the national grid filter

grid_options = [None, 'Yes', 'No']
grid_labels = ['All responses', 'Yes', 'No']

grid_dropdown=alt.binding_select(
    options= grid_options, 
    labels = grid_labels, 
    name = "Is the household connected to the national grid?  ")
grid_select=alt.selection_single(
    fields=['hh_grid'],
    bind=grid_dropdown)

#chart

chart = chart.mark_bar(color = '#2980B9') + chart.mark_text(
    align = 'center', 
    baseline='bottom',
    size = 15
).encode(
    text = alt.Text('sum(pct):Q', 
                    format = '.2%')
)

chart = (chart
).add_selection( # Sixth, cookstove filter
    cookstove_select
).transform_filter(
    cookstove_select
).add_selection( # Third, grid connection filter
    grid_select
).transform_filter(
    grid_select
).add_selection( # First, locality filter
    locality_select
).transform_filter(
    locality_select
).add_selection(
    tier_select
).transform_filter( # Tier filter
    tier_select
)

chart = chart.properties(
    height = 500,
    width = 800,
    title={
      "text": ["Primary Sources of Cooking Fuel"],
      "color": "black",
        "font": 'Times New Roman'
    }
)

final = alt.concat(chart,
    title=alt.TitleParams(
        ['', '',  
         'This chart includes responses from 81.77% of households in the Kenya MTF survey sample (total size = 4,590).',
         'Use the dropdown filters to interact with the data.'],
        baseline='bottom',
        orient='bottom',
        anchor='start',
        font = 'Times New Roman',
        fontWeight='normal',
        fontStyle = "italic",
        fontSize=15)
)

final = final.configure(font = 'Times New Roman')
final

alt.ConcatChart(...)

In [26]:
df.shape[0] / kenya_mtf.shape[0]

0.8177621455264893

In [28]:
final.save('Primary Sources of Cooking Fuel.html')

In [29]:
final.save('Primary Sources of Cooking Fuel.json')

In [21]:
source

key elc_cap_tier elc_durd_tier elc_dure_tier elc_rel_tier elc_qual_tier  \
45    NaN       Tier 5        Tier 5        Tier 3       Tier 4        Tier 5   
94    NaN       Tier 0        Tier 3        Tier 5          NaN        Tier 5   
139   NaN       Tier 5        Tier 5        Tier 5       Tier 4        Tier 5   
146   NaN       Tier 2        Tier 3        Tier 5          NaN        Tier 5   
171   NaN       Tier 1        Tier 3        Tier 5          NaN        Tier 5   
...   ...          ...           ...           ...          ...           ...   
4186  NaN       Tier 1        Tier 2        Tier 5          NaN        Tier 5   
4240  NaN       Tier 4        Tier 5        Tier 5          NaN        Tier 5   
4290  NaN       Tier 1        Tier 3        Tier 5          NaN        Tier 5   
4435  NaN       Tier 0        Tier 5        Tier 5          NaN        Tier 5   
4460  NaN       Tier 2        Tier 2        Tier 5          NaN        Tier 5   

      elc_leg_tier elc_sft_tier                      elc_affd_tier  \
45             5.0       Tier 5  Electricity: affordability Tier 2   
94             NaN          NaN  Electricity: affordability Tier 2   
139            5.0       Tier 5  Electricity: affordability Tier 5   
146            NaN          NaN  Electricity: affordability Tier 5   
171            NaN          NaN  Electricity: affordability Tier 5   
...            ...          ...                                ...   
4186           NaN          NaN  Electricity: affordability Tier 5   
4240           NaN          NaN  Electricity: affordability Tier 5   
4290           NaN          NaN  Electricity: affordability Tier 5   
4435           NaN          NaN  Electricity: affordability Tier 2   
4460           NaN          NaN  Electricity: affordability Tier 5   

     elc_aggr_tier  ...                  solar_problem north_14counties  \
45          Tier 2  ...  Duration of service too short                1   
94          Tier 0  ...               Quality of light                1   
139         Tier 4  ...                  Too expensive                1   
146         Tier 2  ...               Quality of light                0   
171         Tier 1  ...  Duration of service too short                0   
...            ...  ...                            ...              ...   
4186        Tier 1  ...               Quality of light                0   
4240        Tier 4  ...               Breaks too often                0   
4290        Tier 1  ...  Duration of service too short                0   
4435        Tier 0  ...                  Too expensive                1   
4460        Tier 2  ...                    No problems                0   

                                              child_sch  \
45                                                  NaN   
94    Household has children, but they are not atten...   
139                                                 NaN   
146                                                 NaN   
171                                                 NaN   
...                                                 ...   
4186       Household has grandchildren attending school   
4240                                                NaN   
4290                                                NaN   
4435            Household has children attending school   
4460            Household has children attending school   

         Primary_stove_type Primary_1st_fuel Primary_2nd_fuel  \
45    Three stone/Open fire         Firewood   Not applicable   
94    Three stone/Open fire         Firewood         Firewood   
139      Manufactured stove         Kerosene   Not applicable   
146      Manufactured stove         Kerosene   Not applicable   
171      Manufactured stove         Kerosene   Not applicable   
...                     ...              ...              ...   
4186  Three stone/Open fire         Firewood         Firewood   
4240     Manufactured stove         Charcoal   Not applicable 

In [18]:
df.shape[0] / 4590

0.020261437908496733

In [23]:
#fuel stove
alt.data_transformers.disable_max_rows()
source = kenya_mtf[kenya_mtf[['Primary_stove_type', 'Primary_1st_fuel']].notnull().all(1)]

c_1 = source['Primary_1st_fuel'] != 'NaN'
c_2 = source['Primary_stove_type'] != 'NaN'

source = source[conjunction(c_1,c_2)]
df = source[['elc_aggr_tier', 'Primary_stove_type', 'Primary_1st_fuel', 'locality_ur', 'sexhead', 
             'a_8_sch_curr', 'child_sch', 'hh_grid', 'c_c_159', 'elc_access']]

df

elc_aggr_tier      Primary_stove_type Primary_1st_fuel locality_ur  \
0           Tier 0   Three stone/Open fire   Not applicable       Urban   
1           Tier 5      Manufactured stove  LPG/cooking gas       Urban   
2           Tier 2   Three stone/Open fire         Firewood       Rural   
3           Tier 0  Other Self-Built Stove         Firewood       Rural   
5           Tier 3   Three stone/Open fire         Charcoal       Rural   
...            ...                     ...              ...         ...   
4543        Tier 3      Manufactured stove         Charcoal       Urban   
4544        Tier 0   Three stone/Open fire         Firewood       Rural   
4545        Tier 0   Three stone/Open fire         Firewood       Rural   
4546        Tier 0   Three stone/Open fire         Firewood       Rural   
4547        Tier 1   Three stone/Open fire         Firewood       Rural   

     sexhead a_8_sch_curr                                          child_sch  \
0       Male           No                                                NaN   
1     Female          NaN                                                NaN   
2       Male           No                                                NaN   
3       Male          Yes            Household has children attending school   
5       Male           No                                                NaN   
...      ...          ...                                                ...   
4543  Female           No  Household has children, but they are not atten...   
4544  Female          Yes            Household has children attending school   
4545    Male           No                                                NaN   
4546    Male           No  Household has children, but they are not atten...   
4547    Male           No                                                NaN   

     hh_grid                        c_c_159 elc_access  
0         No                 No electricity         No  
1        Yes                  National grid        Yes  
2         No              Solar Home System        Yes  
3         No                          Other        Yes  
5        Yes                  National grid        Yes  
...      ...                            ...        ...  
4543     Yes                  National grid        Yes  
4544      No                 No electricity         No  
4545      No                 No electricity         No  
4546      No                 No electricity         No  
4547      No  Solar Lantern/Lighting System        Yes  

[4034 rows x 10 columns]

In [29]:
# primary stove type

alt.data_transformers.disable_max_rows()
source = kenya_mtf[kenya_mtf[['Primary_stove_type', 'Primary_1st_fuel']].notnull().all(1)]

c_1 = source['Primary_1st_fuel'] != 'NaN'
c_2 = source['Primary_stove_type'] != 'NaN'

source = source[conjunction(c_1,c_2)]
df = source[['elc_aggr_tier', 'Primary_stove_type', 'Primary_1st_fuel', 'locality_ur', 'sexhead', 
             'a_8_sch_curr', 'child_sch', 'hh_grid', 'c_c_159', 'elc_access']]
#chart 

chart = alt.Chart(df).transform_joinaggregate(
    total = 'count(*)'
).transform_calculate(
    pct = '1 / datum.total'
).encode(
    x = alt.X('Primary_stove_type',
              sort=alt.EncodingSortField(field="Primary_stove_type", 
                                         op="count", 
                                         order='descending'),
              axis = alt.Axis(title = " ")),
    y = alt.Y('sum(pct):Q', axis = alt.Axis(title = '', format = '%')),
    tooltip = 'Primary_stove_type'
)

#Locality filter
locality_options = [None, 'Urban', 'Rural']
locality_labels = ['National', 'Urban', 'Rural']

locality_dropdown=alt.binding_select(
    options= locality_options, 
    labels = locality_labels, 
    name = "Locality Breakdown  ")
locality_select=alt.selection_single(
    fields=['locality_ur'],
    bind=locality_dropdown)

#Tier filter
tiers = [None, 'Tier 0', 'Tier 1', 'Tier 2', 'Tier 3', 'Tier 4' ]
tier_labels = ['All Tiers', 'Tier 0', 'Tier 1', 'Tier 2', 'Tier 3', 'Tier 4']
tier_dropdown=alt.binding_select(options=tiers, labels = tier_labels, name = "Electricity Tier  ")
tier_select=alt.selection_single(fields=['elc_aggr_tier'],
                                bind=tier_dropdown)

# Primary cooking fuel

cooking_options = [None, 'Firewood', 'Charcoal', 'LPG/cooking gas', 'Kerosene']
cooking_labels = ['All responses', 'Firewood', 'Charcoal', 'LPG/cooking gas', 'Kerosene']

cooking_dropdown = alt.binding_select(
    options = cooking_options, 
    labels = cooking_labels, 
    name = "Primary source of cooking fuel  ")

cooking_select=alt.selection_single(
    fields=['Primary_1st_fuel'],
    bind=cooking_dropdown)

# Primary cookstove filter

cookstove_options = [None, 'Three stone/Open fire',
                'Manufactured stove',
                'Other Self-Built Stove',
                'Other']

cookstove_labels = ['All responses', 'Three stone/Open fire',
                'Manufactured stove',
                'Self-Built Stove',
                'Other']

cookstove_dropdown = alt.binding_select(
    options = cookstove_options, 
    labels = cookstove_labels, 
    name = "Primary cookstove  ")

cookstove_select=alt.selection_single(
    fields=['Primary_stove_type'],
    bind=cookstove_dropdown)

# Primary lighting filter 

lighting_options = [None, 
                    'National grid',
                   'Rechargeable Battery',
                   'No electricity', 
                   'Solar Lantern/Lighting System',
                   'Solar Home System',
                   'Generator (Connecting one or more households)',
                   'Other']

lighting_labels = ['All responses', 
                   'National grid',
                   'Rechargeable Battery',
                   'No electricity',
                   'Solar Lantern/Lighting System',
                   'Solar Home System',
                   'Generator',
                   'Other']

lighting_dropdown = alt.binding_select(
    options = lighting_options, 
    labels = lighting_labels, 
    name = "Primary source of electricity  ")

lighting_select=alt.selection_single(
    fields=['c_c_156'],
    bind=lighting_dropdown)

# Connected to the national grid filter

grid_options = [None, 'Yes', 'No']
grid_labels = ['All responses', 'Yes', 'No']

grid_dropdown=alt.binding_select(
    options= grid_options, 
    labels = grid_labels, 
    name = "Is the household connected to the national grid?  ")
grid_select=alt.selection_single(
    fields=['hh_grid'],
    bind=grid_dropdown)

#chart

chart = chart.mark_bar(color = '#2980B9') + chart.mark_text(
    align = 'center', 
    baseline='bottom',
    size = 15
).encode(
    text = alt.Text('sum(pct):Q', 
                    format = '.2%')
)

chart = (chart
).add_selection( # Fifth, cooking fuel filter
    cooking_select
).transform_filter(
    cooking_select 
).add_selection( # Third, grid connection filter
    grid_select
).transform_filter(
    grid_select
).add_selection( # First, locality filter
    locality_select
).transform_filter(
    locality_select
).add_selection(
    tier_select
).transform_filter( # Tier filter
    tier_select
)

chart = chart.properties(
    height = 500,
    width = 800,
    title={
      "text": ["Primary Stove Type"],
      "color": "black",
        "font": 'Times New Roman'
    }
)

final = alt.concat(chart,
    title=alt.TitleParams(
        ['', '',  
         'This chart includes responses from 88.67% of households in the Kenya MTF survey sample (total size = 4,590).',
         'Use the dropdown filters to interact with the data.'],
        baseline='bottom',
        orient='bottom',
        anchor='start',
        font = 'Times New Roman',
        fontWeight='normal',
        fontStyle = "italic",
        fontSize=15)
)

final = final.configure(font = 'Times New Roman')
final

alt.ConcatChart(...)

In [27]:
df.shape[0]/kenya_mtf.shape[0]

0.8867883051220048

In [30]:
final.save('Primary Stove Type.html')

In [32]:
final.save('Primary Stove Type.json')

In [10]:
# primary lighting

alt.data_transformers.disable_max_rows()
source = kenya_mtf[kenya_mtf[['c_c_156', 'locality_ur', 'elc_access', 'Primary_1st_fuel', 'Primary_stove_type']].notnull().all(1)]

# data source

col1 = source['locality_ur'] != 'NaN'
col2 = source['elc_access'] != 'NaN'
col3 = source['c_c_156'] != 'NaN'
col4 = source['Primary_1st_fuel'] != 'NaN'
col5 = source['Primary_stove_type'] != 'NaN'

source = source[conjunction(col1,col2, col3, col4, col5)]
df = source[['elc_aggr_tier', 'locality_ur',
             'Primary_1st_fuel', 'Primary_stove_type', 
             'hh_grid', 'c_c_156', 'elc_access']]
#chart 

chart = alt.Chart(df).transform_joinaggregate(
    total = 'count(*)'
).transform_calculate(
    pct = '1 / datum.total'
).encode(
    x = alt.X('c_c_156',
              sort=alt.EncodingSortField(field="c_c_156", 
                                         op="count", 
                                         order='descending'),
              axis = alt.Axis(title = " ")),
    y = alt.Y('sum(pct):Q', axis = alt.Axis(title = '', format = '%')),
    tooltip = 'c_c_156'
)

#Locality filter
locality_options = [None, 'Urban', 'Rural']
locality_labels = ['National', 'Urban', 'Rural']

locality_dropdown=alt.binding_select(
    options= locality_options, 
    labels = locality_labels, 
    name = "Locality Breakdown  ")
locality_select=alt.selection_single(
    fields=['locality_ur'],
    bind=locality_dropdown)

#Tier filter
tiers = [None, 'Tier 0', 'Tier 1', 'Tier 2', 'Tier 3', 'Tier 4' ]
tier_labels = ['All Tiers', 'Tier 0', 'Tier 1', 'Tier 2', 'Tier 3', 'Tier 4']
tier_dropdown=alt.binding_select(options=tiers, labels = tier_labels, name = "Electricity Tier  ")
tier_select=alt.selection_single(fields=['elc_aggr_tier'],
                                bind=tier_dropdown)

# Primary cooking fuel

cooking_options = [None, 'Firewood', 'Charcoal', 'LPG/cooking gas', 'Kerosene']

cooking_labels = ['All responses', 'Firewood', 'Charcoal', 'LPG/cooking gas', 'Kerosene']

cooking_dropdown = alt.binding_select(
    options = cooking_options, 
    labels = cooking_labels, 
    name = "Primary source of cooking fuel  ")

cooking_select=alt.selection_single(
    fields=['Primary_1st_fuel'],
    bind=cooking_dropdown)

# Primary cookstove filter

cookstove_options = [None, 'Three stone/Open fire',
                'Manufactured stove',
                'Other Self-Built Stove',
                'Other']

cookstove_labels = ['All responses', 'Three stone/Open fire',
                'Manufactured stove',
                'Self-Built Stove',
                'Other']

cookstove_dropdown = alt.binding_select(
    options = cookstove_options, 
    labels = cookstove_labels, 
    name = "Primary cookstove  ")

cookstove_select=alt.selection_single(
    fields=['Primary_stove_type'],
    bind=cookstove_dropdown)

# Primary lighting filter 

lighting_options = [None, 
                    'National grid',
                   'Rechargeable Battery',
                   'No electricity', 
                   'Solar Lantern/Lighting System',
                   'Solar Home System',
                   'Generator (Connecting one or more households)',
                   'Other']

lighting_labels = ['All responses', 
                   'National grid',
                   'Rechargeable Battery',
                   'No electricity',
                   'Solar Lantern/Lighting System',
                   'Solar Home System',
                   'Generator',
                   'Other']

lighting_dropdown = alt.binding_select(
    options = lighting_options, 
    labels = lighting_labels, 
    name = "Primary source of electricity  ")

lighting_select=alt.selection_single(
    fields=['c_c_159'],
    bind=lighting_dropdown)

# Connected to the national grid filter

grid_options = [None, 'Yes', 'No']
grid_labels = ['All responses', 'Yes', 'No']

grid_dropdown=alt.binding_select(
    options= grid_options, 
    labels = grid_labels, 
    name = "Is the household connected to the national grid?  ")
grid_select=alt.selection_single(
    fields=['hh_grid'],
    bind=grid_dropdown)

#chart

chart = chart.mark_bar(color = '#2980B9') + chart.mark_text(
    align = 'center', 
    baseline='bottom',
    size = 15
).encode(
    text = alt.Text('sum(pct):Q', 
                    format = '.2%')
)

chart = (chart
).add_selection( # Sixth, cookstove filter
    cookstove_select
).transform_filter(
    cookstove_select
).add_selection( # Fifth, cooking fuel filter
    cooking_select
).transform_filter(
    cooking_select 
).add_selection( # Third, grid connection filter
    grid_select
).transform_filter(
    grid_select
).add_selection( # First, locality filter
    locality_select
).transform_filter(
    locality_select
).add_selection(
    tier_select
).transform_filter( # Tier filter
    tier_select
)

chart = chart.properties(
    height = 500,
    width = 800,
    title={
      "text": ["Primary Source of Lighting Prior to Solar"],
      "color": "black",
        "font": 'Times New Roman'
    }
)

final = alt.concat(chart,
    title=alt.TitleParams(
        ['', '',  
         'This chart includes responses from 2.04% of households in the Kenya MTF survey sample (total size = 4,590).',
         'Use the dropdown filters to interact with the data.'],
        baseline='bottom',
        orient='bottom',
        anchor='start',
        font = 'Times New Roman',
        fontWeight='normal',
        fontStyle = "italic",
        fontSize=15)
)

final = final.configure(font = 'Times New Roman')
final

alt.ConcatChart(...)

In [127]:
final.save('Primary Source of Lighting Prior to Solar.html')

In [128]:
final.save('Primary Source of Lighting Prior to Solar.json')

In [11]:
# Subtopic 2: Grid Electricity Access by Tier
# Variables: hh_grid

alt.data_transformers.disable_max_rows()
source = kenya_mtf[kenya_mtf[['c_c_159', 'locality_ur', 'elc_access', 'Primary_1st_fuel', 'Primary_stove_type']].notnull().all(1)]

# data source

col1 = source['locality_ur'] != 'NaN'
col2 = source['elc_access'] != 'NaN'
col3 = source['c_c_159'] != 'NaN'
col4 = source['Primary_1st_fuel'] != 'NaN'
col5 = source['Primary_stove_type'] != 'NaN'

source = source[conjunction(col1,col2, col3, col4, col5)]
df = source[['elc_aggr_tier', 'locality_ur',
             'Primary_1st_fuel', 'Primary_stove_type', 
             'hh_grid', 'c_c_159', 'elc_access']]

cookstove_options = [None, 'Three stone/Open fire',
                'Manufactured stove',
                'Other Self-Built Stove',
                'Other']

cookstove_labels = ['All responses', 'Three stone/Open fire',
                'Manufactured stove',
                'Self-Built Stove',
                'Other']

cookstove_dropdown = alt.binding_select(
    options = cookstove_options, 
    labels = cookstove_labels, 
    name = "Primary cookstove  ")

cookstove_select=alt.selection_single(
    fields=['Primary_stove_type'],
    bind=cookstove_dropdown)

# chart

energy_access2 = alt.Chart(df).transform_joinaggregate(
    total = 'count(*)'
).transform_calculate(
    pct = '1 / datum.total'
).encode(
    x = alt.X('elc_aggr_tier', axis = alt.Axis(title = '')),
    y = alt.Y('sum(pct):Q', axis = alt.Axis(title = "", format = '%')),
    color = alt.Color('hh_grid:N', 
                      scale = alt.Scale(domain=['Yes', 'No'], 
                                        range=["#003366", "#FFAE19"])),
    tooltip = [alt.Tooltip('hh_grid:N', title = "Is the household connected to the national grid?"), 
               alt.Tooltip('sum(pct):Q', format = '.2%', title = "Percentage")]
)
     
locality_options = [None, 'Urban', 'Rural']
locality_labels = ['National', 'Urban', 'Rural']

locality_dropdown=alt.binding_select(
    options= locality_options, 
    labels = locality_labels, 
    name = "Locality Breakdown  ")
locality_select=alt.selection_single(
    fields=['locality_ur'],
    bind=locality_dropdown)


grid_acc_tier = (energy_access2.mark_bar() + energy_access2.mark_text(
    align = 'center', baseline='bottom', size = 15, dy = -4
).encode(
    text = alt.Text('sum(pct):Q', format = '.2%')
)).add_selection(
    locality_select
).transform_filter(
    locality_select)

chart = (grid_acc_tier
).add_selection( # Sixth, cookstove filter
    cookstove_select
).transform_filter(
    cookstove_select
).add_selection( # Fifth, cooking fuel filter
    cooking_select
).transform_filter(
    cooking_select
).add_selection( # Fourth, primary source of lighting
    lighting_select
).transform_filter(
    lighting_select  
).add_selection( # First, locality filter
    locality_select
).transform_filter(
    locality_select
)

chart = chart.properties(
    height = 500,
    width = 800,
    title={
      "text": ["Grid Electricity Access by Tier"],
      "color": "black",
        "font": 'Times New Roman'
    }
)

final = alt.concat(chart,
    title=alt.TitleParams(
        ['', '',  
         'This chart includes responses from 81.77% of households in the Kenya MTF survey sample (total size = 4,590).',
         'Use the dropdown filters to interact with the data.'],
        baseline='bottom',
        orient='bottom',
        anchor='start',
        font = 'Times New Roman',
        fontWeight='normal',
        fontStyle = "italic",
        fontSize=15)
)

final = final.configure(font = 'Times New Roman')
final

alt.ConcatChart(...)

In [68]:
df.shape[0] / kenya_mtf.shape[0]

0.8177621455264893

In [12]:
final.save('Grid Electricity Access by Tier.html')

In [13]:
final.save('Grid Electricity Access by Tier.json')

In [14]:
#fuel stove
alt.data_transformers.disable_max_rows()
source = kenya_mtf[kenya_mtf[['Primary_stove_type', 'Primary_1st_fuel']].notnull().all(1)]

c_1 = source['Primary_1st_fuel'] != 'NaN'
c_2 = source['Primary_stove_type'] != 'NaN'

source = source[conjunction(c_1,c_2)]
df = source[['elc_aggr_tier', 'Primary_stove_type', 'Primary_1st_fuel', 'locality_ur', 'sexhead', 
             'a_8_sch_curr', 'child_sch', 'hh_grid', 'c_c_159', 'elc_access']]

# Configure common options
base = alt.Chart(df).transform_aggregate(
    cookstove_count='count()',
    groupby=['Primary_1st_fuel', 'Primary_stove_type']
).encode(
    alt.Y('Primary_1st_fuel:O', scale=alt.Scale(paddingInner=0), title = "Primary Cooking Fuel Types"),
    alt.X('Primary_stove_type:O', 
        sort=alt.EncodingSortField(field="Primary_stove_type", op="count", order='descending'),
          scale=alt.Scale(paddingInner=0), 
          title = "Primary Stove Types"),
)

# Configure heatmap
heatmap = base.mark_rect().encode(
    color=alt.Color('cookstove_count:Q',
        scale=alt.Scale(scheme='blues'),
        legend=None
    )
)

# Configure text
text = base.mark_text(baseline='middle', size = 15
).transform_joinaggregate(
    count = 'count(cookstove_count)',
    groupby = ['Primary_1st_fuel', 'Primary_stove_type']
).transform_calculate(
    pct = alt.datum.cookstove_count / df.shape[0]
).encode(
    text=alt.Text('pct:Q', format = '.2%'),
    color=alt.condition(
        alt.datum.cookstove_count < 100,
        alt.value('black'),
        alt.value('white')
    )
)

# Locality Filter

locality_options = [None, 'Urban', 'Rural']
locality_labels = ['National', 'Urban', 'Rural']

locality_dropdown=alt.binding_select(
    options= locality_options, 
    labels = locality_labels, 
    name = "Locality Breakdown  ")
locality_select=alt.selection_single(
    fields=['locality_ur'],
    bind=locality_dropdown)


# Primary cooking fuel

cooking_options = [None, 'Firewood', 'Charcoal', 'LPG/cooking gas', 'Kerosene', 
                    'Biomass Briquette', 'Electricity', 'Biogas', 
                    'Coal/lignite']

cooking_labels = ['All responses', 'Firewood', 'Charcoal', 'LPG/cooking gas', 'Kerosene',
                    'Biomass Briquette', 'Electricity', 'Biogas', 
                    'Coal/lignite']

cooking_dropdown = alt.binding_select(
    options = cooking_options, 
    labels = cooking_labels, 
    name = "Primary source of cooking fuel  ")

cooking_select=alt.selection_single(
    fields=['Primary_1st_fuel'],
    bind=cooking_dropdown)

# Primary cookstove filter

cookstove_options = [None, 'Three stone/Open fire',
                'Manufactured stove',
                'Other Self-Built Stove',
                'Other']

cookstove_labels = ['All responses', 'Three stone/Open fire',
                'Manufactured stove',
                'Other Self-Built Stove',
                'Other']

cookstove_dropdown = alt.binding_select(
    options = cookstove_options, 
    labels = cookstove_labels, 
    name = "Primary cookstove  ")

cookstove_select=alt.selection_single(
    fields=['Primary_stove_type'],
    bind=cookstove_dropdown)

# Primary lighting filter 

lighting_options = [None, 'National grid',
                   'Rechargeable Battery',
                   'No electricity', 
                   'Solar Lantern/Lighting System',
                   'Solar Home System',
                   'Generator (Connecting one or more households)',
                   'Other']

lighting_labels = ['All responses', 'National grid',
                   'Rechargeable Battery',
                   'No electricity', 
                   'Solar Lantern/Lighting System',
                   'Solar Home System',
                   'Generator',
                   'Other']

lighting_dropdown = alt.binding_select(
    options = lighting_options, 
    labels = lighting_labels, 
    name = "Primary source of electricity  ")

lighting_select=alt.selection_single(
    fields=['c_c_159'], # 156?
    bind=lighting_dropdown)

# Connected to the national grid filter

grid_options = [None, 'Yes', 'No']
grid_labels = ['All responses', 'Yes', 'No']

grid_dropdown=alt.binding_select(
    options= grid_options, 
    labels = grid_labels, 
    name = "Is the household connected to the national grid?  ")
grid_select=alt.selection_single(
    fields=['hh_grid'],
    bind=grid_dropdown)


# Tier filter

tiers = [None, 'Tier 0', 'Tier 1', 'Tier 2', 'Tier 3', 'Tier 4', 'Tier 5']
tier_labels = ['All Tiers', 'Tier 0', 'Tier 1', 'Tier 2', 'Tier 3', 'Tier 4', 'Tier 5']
tier_dropdown=alt.binding_select(options=tiers, labels = tier_labels, name = "Electricity Tier  ")
tier_select=alt.selection_single(fields=['elc_aggr_tier'],
                                bind=tier_dropdown)

# Draw the chart
heatmap_fuel_stove = (heatmap + text
).add_selection( # Eighth, tier filter
    tier_select
).transform_filter(
    tier_select 
).add_selection( # Fourth, primary source of lighting
    lighting_select
).transform_filter(
    lighting_select  
).add_selection( # Third, grid connection filter
    grid_select
).transform_filter(
    grid_select
).add_selection( # First, locality filter
    locality_select
).transform_filter(
    locality_select
)

chart = heatmap_fuel_stove.properties(
    height = 500,
    width = 800,
    title={
      "text": ["Primary Cooking Fuel vs. Primary Cookstove"],
      "color": "black",
        "font": 'Times New Roman'
    }
)

final = alt.concat(chart,
    title=alt.TitleParams(
        ['', '',  
         'This chart includes responses from 88.69% of households in the Kenya MTF survey sample (total size = 4,590).',
         'Use the dropdown filters to interact with the data.'],
        baseline='bottom',
        orient='bottom',
        anchor='start',
        font = 'Times New Roman',
        fontWeight='normal',
        fontStyle = "italic",
        fontSize=15)
)

final = final.configure(font = 'Times New Roman').configure_title(
    fontSize=20, offset=5, orient='top', anchor='middle'
)
final

alt.ConcatChart(...)

In [130]:
df.shape[0]/kenya_mtf.shape[0]

0.8867883051220048

In [15]:
final.save("Primary Cooking Fuel vs. Primary Cookstove.html")

In [16]:
final.save("Primary Cooking Fuel vs. Primary Cookstove.json")

In [13]:
#fuel stove
alt.data_transformers.disable_max_rows()
source = kenya_mtf[kenya_mtf[['Secondary_1st_fuel', 'Primary_1st_fuel']].notnull().all(1)]

c_1 = source['Primary_1st_fuel'] != 'NaN'
c_2 = source['Secondary_1st_fuel'] != 'NaN'

source = source[conjunction(c_1,c_2)]
df = source[['elc_aggr_tier', 'Primary_stove_type', 'Primary_1st_fuel', 'locality_ur', 'sexhead', 'Secondary_1st_fuel',
             'a_8_sch_curr', 'child_sch', 'hh_grid', 'c_c_159', 'elc_access']]

# Configure common options
base = alt.Chart(df).transform_aggregate(
    cookstove_count='count()',
    groupby=['Primary_1st_fuel', 'Secondary_1st_fuel']
).encode(
    alt.Y('Primary_1st_fuel:O', scale=alt.Scale(paddingInner=0), title = "Primary Cooking Fuel Types"),
    alt.X('Secondary_1st_fuel:O', 
        sort=alt.EncodingSortField(field="Primary_stove_type", op="count", order='descending'),
          scale=alt.Scale(paddingInner=0), title = "Secondary Cooking Fuel Types"),
)

# Configure heatmap
heatmap = base.mark_rect().encode(
    color=alt.Color('cookstove_count:Q',
        scale=alt.Scale(scheme='blues'),
        legend=None
    )
)

# Configure text
text = base.mark_text(baseline='middle', size = 15
).transform_joinaggregate(
    count = 'count(cookstove_count)',
    groupby = ['Primary_1st_fuel', 'Secondary_1st_fuel']
).transform_calculate(
    pct = alt.datum.cookstove_count / df.shape[0]
).encode(
    text=alt.Text('pct:Q', format = '.2%'),
    color=alt.condition(
        alt.datum.cookstove_count < 100,
        alt.value('black'),
        alt.value('white')
    )
)

# Locality Filter

locality_options = [None, 'Urban', 'Rural']
locality_labels = ['National', 'Urban', 'Rural']

locality_dropdown=alt.binding_select(
    options= locality_options, 
    labels = locality_labels, 
    name = "Locality Breakdown  ")
locality_select=alt.selection_single(
    fields=['locality_ur'],
    bind=locality_dropdown)


# Primary cookstove filter

cookstove_options = [None, 'Three stone/Open fire',
                'Manufactured stove',
                'Other Self-Built Stove',
                'Other']

cookstove_labels = ['All responses', 'Three stone/Open fire',
                'Manufactured stove',
                'Other Self-Built Stove',
                'Other']

cookstove_dropdown = alt.binding_select(
    options = cookstove_options, 
    labels = cookstove_labels, 
    name = "Primary cookstove  ")

cookstove_select=alt.selection_single(
    fields=['Primary_stove_type'],
    bind=cookstove_dropdown)

# Primary lighting filter 

lighting_options = [None, 'National grid',
                   'Rechargeable Battery',
                   'No electricity', 
                   'Solar Lantern/Lighting System',
                   'Solar Home System',
                   'Generator (Connecting one or more households)',
                   'Other']

lighting_labels = ['All responses', 'National grid',
                   'Rechargeable Battery',
                   'No electricity', 
                   'Solar Lantern/Lighting System',
                   'Solar Home System',
                   'Generator',
                   'Other']

lighting_dropdown = alt.binding_select(
    options = lighting_options, 
    labels = lighting_labels, 
    name = "Primary source of electricity  ")

lighting_select=alt.selection_single(
    fields=['c_c_159'],
    bind=lighting_dropdown)

# Connected to the national grid filter

grid_options = [None, 'Yes', 'No']
grid_labels = ['All responses', 'Yes', 'No']

grid_dropdown=alt.binding_select(
    options= grid_options, 
    labels = grid_labels, 
    name = "Is the household connected to the national grid?  ")
grid_select=alt.selection_single(
    fields=['hh_grid'],
    bind=grid_dropdown)


# Tier filter

tiers = [None, 'Tier 0', 'Tier 1', 'Tier 2', 'Tier 3', 'Tier 4', 'Tier 5']
tier_labels = ['All Tiers', 'Tier 0', 'Tier 1', 'Tier 2', 'Tier 3', 'Tier 4', 'Tier 5']
tier_dropdown=alt.binding_select(options=tiers, labels = tier_labels, name = "Electricity Tier  ")
tier_select=alt.selection_single(fields=['elc_aggr_tier'],
                                bind=tier_dropdown)

# Draw the chart
heatmap_fuel_stove = (heatmap + text
).add_selection( # Eighth, tier filter
    tier_select
).transform_filter(
    tier_select 
).add_selection( # Fourth, primary source of lighting
    lighting_select
).transform_filter(
    lighting_select  
).add_selection( # Third, grid connection filter
    grid_select
).transform_filter(
    grid_select
).add_selection( # First, locality filter
    locality_select
).transform_filter(
    locality_select
)

chart = heatmap_fuel_stove.properties(
    height = 500,
    width = 800,
    title={
      "text": ["Primary vs. Secondary Cooking Fuel Types"],
      "color": "black",
        "font": 'Times New Roman'
    }
)

final = alt.concat(chart,
    title=alt.TitleParams(
        ['', '',  
         'This chart includes responses from 19.81% of households in the Kenya MTF survey sample (total size = 4,590).',
         'Use the dropdown filters to interact with the data.'],
        baseline='bottom',
        orient='bottom',
        anchor='start',
        font = 'Times New Roman',
        fontWeight='normal',
        fontStyle = "italic",
        fontSize=15)
)

final = final.configure(font = 'Times New Roman').configure_title(
    fontSize=20, offset=5, orient='top', anchor='middle'
)
final

alt.ConcatChart(...)

In [114]:
df.shape[0]/kenya_mtf.shape[0]

0.1980655089030556

In [14]:
final.save('Primary vs. Secondary Fuel Types.html')

In [15]:
final.save('Primary vs. Secondary Fuel Types.json')